In [1]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from datetime import datetime
import warnings
import time
import sklearn.preprocessing

pd.set_option("display.max_columns", None)
warnings.filterwarnings(action='ignore')

serviceKey='bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ=='

p7000 ={'serviceKey' :serviceKey,
             'routeId':'200000112','stationId':'228000703'}
class Bus():
    def __init__(self,params):
        self.params=params
        self.bus_time=[]
        
    def repet(self):
        url = 'http://apis.data.go.kr/6410000/busarrivalservice/getBusArrivalItem'
        response = requests.get(url, params=self.params)
        soup=BeautifulSoup(response.text,'xml')
        return soup

        
    def current_buses(self): 
        url = 'http://apis.data.go.kr/6410000/buslocationservice/getBusLocationList'
        mod_params ={'serviceKey' : self.params['serviceKey'],
                  'routeId':self.params['routeId']}

        response=requests.get(url,params=mod_params)
        soup=BeautifulSoup(response.text,'xml')
        locations=sorted([int(x.stationSeq.text) for x in soup.find_all('busLocationList')])
        return locations


def trim_data(df,FileName):
    df['시간'] = df['시간'].apply(pd.to_datetime)
    df['hour']=df['시간'].dt.hour
    df['minute']=df['시간'].dt.minute
    df['second']=df['시간'].dt.second
    df['day'] = df['시간'].dt.weekday 

    mb = sklearn.preprocessing.MultiLabelBinarizer()
    if isinstance(df['운행중인 다른 버스들의 위치'].iloc[0], str):
        df['운행중인 다른 버스들의 위치'] = df['운행중인 다른 버스들의 위치'].apply(eval)
    entity = mb.fit_transform(df['운행중인 다른 버스들의 위치']) 
    lsts=pd.DataFrame(entity,columns=mb.classes_)
    lsts.columns=[f'station{x}' for x in lsts.columns]
    df=pd.concat([df,lsts],axis=1,sort=False).reset_index(drop=True)


    df=df.drop(["운행중인 다른 버스들의 위치"],axis=1)
    
    batch=df.index[df.arrived==1]
    df=df.iloc[:batch[-1]+1,:]
    #7/12 -----------------------------------
    batch=df.index[df.arrived==1]
    temp=0
    for x in batch:
        for y in range(temp,x): 
            df['arrived'][y]=(df['시간'][x]-df['시간'][y]).seconds
            temp=x+1
    for e in batch:
        df['arrived'][e]=0
    # 7/12 -----------------------------------

    df = df.set_index('시간')
    df.to_csv(f'./{FileName}')        # 동일 폴더에 파일이 저장될 거임
    return df


In [2]:
past=4
pBus=Bus(p7000)
for x in range(720): # 시간 설정
    soup=pBus.repet()
    try:
        result=int(soup.resultCode.text)
        arrived=0
        if past!=result:
            if result==0:
                arrived=1
        pBus.bus_time.append([soup.queryTime.text,pBus.current_buses(),arrived])
        past=result
        print(x,"번째 시도: ",pBus.bus_time)
        time.sleep(60)
    except Exception as e:
        continue

df=pd.DataFrame(pBus.bus_time,columns=['시간','운행중인 다른 버스들의 위치','arrived'])

mod_df=trim_data(df,'7000_8.10.csv') # 이름 설정
mod_df

0 번째 시도:  [['2022-08-10 12:22:46.736', [7, 16, 24, 29, 40, 51, 56, 60, 71], 0]]
1 번째 시도:  [['2022-08-10 12:22:46.736', [7, 16, 24, 29, 40, 51, 56, 60, 71], 0], ['2022-08-10 12:23:48.032', [8, 16, 25, 30, 40, 51, 57, 61, 72], 0]]
2 번째 시도:  [['2022-08-10 12:22:46.736', [7, 16, 24, 29, 40, 51, 56, 60, 71], 0], ['2022-08-10 12:23:48.032', [8, 16, 25, 30, 40, 51, 57, 61, 72], 0], ['2022-08-10 12:24:48.203', [8, 17, 25, 31, 40, 51, 59, 62, 73], 0]]
3 번째 시도:  [['2022-08-10 12:22:46.736', [7, 16, 24, 29, 40, 51, 56, 60, 71], 0], ['2022-08-10 12:23:48.032', [8, 16, 25, 30, 40, 51, 57, 61, 72], 0], ['2022-08-10 12:24:48.203', [8, 17, 25, 31, 40, 51, 59, 62, 73], 0], ['2022-08-10 12:25:48.343', [9, 18, 26, 31, 41, 52, 60, 63, 73], 0]]
4 번째 시도:  [['2022-08-10 12:22:46.736', [7, 16, 24, 29, 40, 51, 56, 60, 71], 0], ['2022-08-10 12:23:48.032', [8, 16, 25, 30, 40, 51, 57, 61, 72], 0], ['2022-08-10 12:24:48.203', [8, 17, 25, 31, 40, 51, 59, 62, 73], 0], ['2022-08-10 12:25:48.343', [9, 18, 26, 31, 41, 

15 번째 시도:  [['2022-08-10 12:22:46.736', [7, 16, 24, 29, 40, 51, 56, 60, 71], 0], ['2022-08-10 12:23:48.032', [8, 16, 25, 30, 40, 51, 57, 61, 72], 0], ['2022-08-10 12:24:48.203', [8, 17, 25, 31, 40, 51, 59, 62, 73], 0], ['2022-08-10 12:25:48.343', [9, 18, 26, 31, 41, 52, 60, 63, 73], 0], ['2022-08-10 12:26:48.499', [9, 18, 26, 32, 41, 52, 61, 63, 75], 0], ['2022-08-10 12:27:48.624', [10, 19, 26, 33, 42, 52, 62, 65, 76], 0], ['2022-08-10 12:28:48.795', [10, 19, 26, 33, 42, 52, 63, 65, 76], 0], ['2022-08-10 12:29:52.341', [11, 20, 27, 33, 43, 53, 63, 65, 76], 0], ['2022-08-10 12:30:52.622', [1, 12, 21, 27, 33, 44, 53, 64, 66, 77], 1], ['2022-08-10 12:31:52.731', [2, 13, 21, 28, 34, 45, 54, 65, 66, 79], 0], ['2022-08-10 12:32:52.887', [3, 13, 21, 28, 34, 45, 55, 65, 67, 79], 0], ['2022-08-10 12:33:54.074', [3, 14, 22, 29, 36, 45, 55, 67, 68], 0], ['2022-08-10 12:34:55.230', [4, 14, 22, 29, 37, 46, 56, 68, 68], 0], ['2022-08-10 12:35:56.651', [5, 14, 24, 30, 38, 46, 57, 68, 68], 0], ['2022-

ConnectionError: HTTPConnectionPool(host='apis.data.go.kr', port=80): Max retries exceeded with url: /6410000/busarrivalservice/getBusArrivalItem?serviceKey=bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ%3D%3D&routeId=200000112&stationId=228000703 (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000026B9CFBC6D0>: Failed to establish a new connection: [WinError 10060] 연결된 구성원으로부터 응답이 없어 연결하지 못했거나, 호스트로부터 응답이 없어 연결이 끊어졌습니다'))

In [3]:
past=4
pBus=Bus(p7000)
for x in range(720): # 시간 설정
    soup=pBus.repet()
    try:
        result=int(soup.resultCode.text)
        arrived=0
        if past!=result:
            if result==0:
                arrived=1
        pBus.bus_time.append([soup.queryTime.text,pBus.current_buses(),arrived])
        past=result
        print(x,"번째 시도: ",pBus.bus_time)
        time.sleep(60)
    except Exception as e:
        continue

df=pd.DataFrame(pBus.bus_time,columns=['시간','운행중인 다른 버스들의 위치','arrived'])

mod_df=trim_data(df,'7000_8.10.csv') # 이름 설정
mod_df

0 번째 시도:  [['2022-08-10 14:18:37.694', [8, 18, 27, 37, 49, 63, 73], 0]]
1 번째 시도:  [['2022-08-10 14:18:37.694', [8, 18, 27, 37, 49, 63, 73], 0], ['2022-08-10 14:19:43.038', [9, 19, 27, 38, 50, 63, 74], 0]]


ConnectionError: HTTPConnectionPool(host='apis.data.go.kr', port=80): Max retries exceeded with url: /6410000/busarrivalservice/getBusArrivalItem?serviceKey=bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ%3D%3D&routeId=200000112&stationId=228000703 (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000026B9EACF880>: Failed to establish a new connection: [WinError 10053] 현재 연결은 사용자의 호스트 시스템의 소프트웨어의 의해 중단되었습니다'))

In [4]:
past=4
pBus=Bus(p7000)
for x in range(720): # 시간 설정
    soup=pBus.repet()
    try:
        result=int(soup.resultCode.text)
        arrived=0
        if past!=result:
            if result==0:
                arrived=1
        pBus.bus_time.append([soup.queryTime.text,pBus.current_buses(),arrived])
        past=result
        print(x,"번째 시도: ",pBus.bus_time)
        time.sleep(60)
    except Exception as e:
        continue

df=pd.DataFrame(pBus.bus_time,columns=['시간','운행중인 다른 버스들의 위치','arrived'])

mod_df=trim_data(df,'7000_8.10.csv') # 이름 설정
mod_df

0 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0]]
1 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0]]
2 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0]]
3 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0]]
4 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15,

16 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 64

24 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 64

29 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 64

33 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 64

...

351 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 6

352 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 6

353 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 6

354 번째 시도:  [['2022-08-10 15:22:22.225', [6, 14, 26, 31, 39, 49, 56, 70], 0], ['2022-08-10 15:23:27.240', [7, 14, 26, 32, 40, 49, 56, 70], 0], ['2022-08-10 15:24:28.693', [7, 14, 26, 32, 40, 50, 57, 70], 0], ['2022-08-10 15:25:35.006', [7, 15, 26, 33, 41, 50, 57, 71], 0], ['2022-08-10 15:26:35.412', [8, 15, 26, 34, 41, 51, 57, 72], 0], ['2022-08-10 15:27:39.958', [8, 16, 27, 34, 41, 51, 58, 73], 0], ['2022-08-10 15:28:42.661', [9, 17, 27, 36, 42, 51, 60, 73], 0], ['2022-08-10 15:29:42.817', [9, 18, 27, 37, 43, 52, 60, 74], 0], ['2022-08-10 15:30:42.988', [9, 18, 28, 37, 43, 52, 61, 74], 0], ['2022-08-10 15:31:43.128', [1, 10, 19, 28, 38, 44, 52, 62, 74], 1], ['2022-08-10 15:32:43.236', [1, 10, 19, 29, 38, 45, 52, 63, 75], 0], ['2022-08-10 15:33:43.392', [3, 10, 20, 29, 38, 45, 53, 63, 76], 0], ['2022-08-10 15:34:43.517', [3, 10, 20, 29, 39, 46, 53, 63, 77], 0], ['2022-08-10 15:35:43.798', [5, 11, 21, 30, 39, 46, 54, 63, 78], 0], ['2022-08-10 15:36:43.985', [6, 12, 21, 31, 39, 47, 54, 6

ConnectionError: HTTPConnectionPool(host='apis.data.go.kr', port=80): Max retries exceeded with url: /6410000/busarrivalservice/getBusArrivalItem?serviceKey=bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ%3D%3D&routeId=200000112&stationId=228000703 (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000026B9ECF0D90>: Failed to establish a new connection: [WinError 10060] 연결된 구성원으로부터 응답이 없어 연결하지 못했거나, 호스트로부터 응답이 없어 연결이 끊어졌습니다'))